In [91]:
import pandas as pd
import numpy as np

In [113]:
import holoviews as hv
import hvplot.pandas

https://holoviz.org/tutorial/Composing_Plots.html

In [197]:
menu_data = pd.read_csv('data/8358_1.csv')
menu_data.head(2)

id                                  address   categories  \
0  AVwc_6KEIN2L1WUfrKAH  Cascade Village Mall Across From Target  Pizza Place   
1  AVwc_6KEIN2L1WUfrKAH  Cascade Village Mall Across From Target  Pizza Place   

   city country                                               keys   latitude  \
0  Bend      US  us/or/bend/cascadevillagemallacrossfromtarget/...  44.102665   
1  Bend      US  us/or/bend/cascadevillagemallacrossfromtarget/...  44.102665   

    longitude menuPageURL  menus.amountMax  ...  menus.currency  \
0 -121.300797         NaN            22.50  ...             USD   
1 -121.300797         NaN            18.95  ...             USD   

         menus.dateSeen menus.description    menus.name  \
0  2016-03-31T02:19:42Z               NaN  Bianca Pizza   
1  2016-03-31T02:19:42Z               NaN  Cheese Pizza   

                    name postalCode priceRangeCurrency priceRangeMin  \
0  Little Pizza Paradise      97701                NaN           NaN   
1  Little Pizza Paradise      97701                NaN           NaN   

   priceRangeMax  province  
0            NaN        OR  
1            NaN        OR  

[2 rows x 21 columns]

In [198]:
df = menu_data.loc[:, ['name', 'latitude', 'longitude']].drop_duplicates().copy()
df = df.merge(menu_data.groupby('name').count()["menus.name"], on = ['name'], how = 'inner')
df = df.merge(menu_data.groupby('name').mean()["menus.amountMax"], on = ['name'], how = 'inner')
df = df.rename(columns = {'menus.name': 'items_count', "menus.amountMax" : 'avg_price'})
df['random'] = np.random.randint(1, high=3, size=len(df))
df.describe()

latitude   longitude  items_count   avg_price      random
count  989.000000  989.000000   989.000000  901.000000  989.000000
mean    38.616538  -88.911107     4.568251   10.700072    1.492417
std      4.971874   16.931357     7.519788    7.978397    0.500195
min     18.411826 -157.837461     1.000000    1.000000    1.000000
25%     35.306490  -96.681801     1.000000    6.898378    1.000000
50%     40.094549  -83.010505     2.000000    9.706000    1.000000
75%     41.660583  -75.069113     5.000000   13.000000    2.000000
max     64.854370  -66.024871    96.000000  163.325000    2.000000

In [199]:
df.loc[:, 'easting'], df.loc[:, 'northing'] = hv.util.transform.lon_lat_to_easting_northing(df.longitude,df.latitude)
df.describe()

latitude   longitude  items_count   avg_price      random  \
count  989.000000  989.000000   989.000000  901.000000  989.000000   
mean    38.616538  -88.911107     4.568251   10.700072    1.492417   
std      4.971874   16.931357     7.519788    7.978397    0.500195   
min     18.411826 -157.837461     1.000000    1.000000    1.000000   
25%     35.306490  -96.681801     1.000000    6.898378    1.000000   
50%     40.094549  -83.010505     2.000000    9.706000    1.000000   
75%     41.660583  -75.069113     5.000000   13.000000    2.000000   
max     64.854370  -66.024871    96.000000  163.325000    2.000000   

            easting      northing  
count  9.890000e+02  9.890000e+02  
mean  -9.897539e+06  4.690526e+06  
std    1.884790e+06  7.008845e+05  
min   -1.757039e+07  2.085809e+06  
25%   -1.076257e+07  4.205610e+06  
50%   -9.240687e+06  4.879691e+06  
75%   -8.356655e+06  5.110271e+06  
max   -7.349855e+06  9.570116e+06

#### Play around with color palettes - reverse color palette

In [200]:
import colorcet as cc
from colorcet.plotting import swatch

swatch('CET_L4')

:Image   [x,y]   (z)

In [201]:
mag_cmap = cc.CET_L4[::-1]
swatch("CET_L4_r", mag_cmap)

:Image   [x,y]   (z)

In [202]:
df.hvplot.points(
    x='easting', y='northing', c='random', hover_cols=['city'], 
    cmap=mag_cmap, title='Pizzerias in the US', tiles='OSM',
    line_color='black')

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [easting,northing]   (random)

In [203]:
import xarray as xr
import hvplot.xarray  # noqa: adds hvplot method to xarray objects

In [204]:
import datashader as ds, bokeh

In [205]:
#l = ['easting', 'northing'] #['latitude', 'longitude']

d = df.drop_duplicates(subset = ['latitude', 'longitude']).set_index(['latitude', 'longitude'])
d

name  items_count  \
latitude  longitude                                                     
44.102665 -121.300797              Little Pizza Paradise            2   
34.064563 -118.469017                      The Brentwood            5   
34.101742 -118.301973              Bravo Pizza Hollywood            6   
29.752479 -95.354164                         Lucky's Pub            1   
41.648278 -70.291345                      Roadhouse Cafe            2   
...                                                  ...          ...   
39.817155 -86.228120                      Rick's Cabaret            1   
41.422509 -87.237723            Mighty Mick's Pub & Cafe            1   
38.568717 -92.161596   Prison Brews Brewery & Restaurant            7   
39.996444 -76.845180                      Moonlight Cafe            2   
37.693160 -77.437440                              Guidos            1   

                       avg_price  random       easting      northing  
latitude  longitude                                                   
44.102665 -121.300797  20.725000       1 -1.350314e+07  5.481344e+06  
34.064563 -118.469017  13.600000       2 -1.318791e+07  4.037475e+06  
34.101742 -118.301973  11.490000       1 -1.316932e+07  4.042472e+06  
29.752479 -95.354164    9.950000       2 -1.061478e+07  3.471773e+06  
41.648278 -70.291345    9.950000       2 -7.824797e+06  5.108438e+06  
...                          ...     ...           ...           ...  
39.817155 -86.228120    8.000000       2 -9.598870e+06  4.839407e+06  
41.422509 -87.237723         NaN       2 -9.711259e+06  5.074863e+06  
38.568717 -92.161596   11.156667       1 -1.025938e+07  4.660081e+06  
39.996444 -76.845180   12.500000       1 -8.554366e+06  4.865426e+06  
37.693160 -77.437440         NaN       2 -8.620296e+06  4.536170e+06  

[988 rows x 6 columns]

In [206]:
dd = xr.Dataset.from_dataframe(d)
#dd.hvplot.image(x='longitude', y='latitude', z='random', cmap='kbc_r', coastline=True, rtol = 0.0001, rasterize=True)
dd.hvplot.image(x='longitude', y='latitude', z='items_count', cmap='kbc_r', coastline=True, rasterize=True)
#dd.hvplot.quadmesh(x='longitude', y='latitude', z='items_count', cmap='kbc_r') #, groupby = 'random'

:DynamicMap   []
   :Overlay
      .Image.I     :Image   [longitude,latitude]   (items_count)
      .Coastline.I :Feature   [Longitude,Latitude]

In [196]:
title = 'Putting things together, maybe'

rasterized_pop = dd.hvplot.image(
    x='longitude', y='latitude', z='random', coastline=True, rtol = 0.0001,
    rasterize=True, cmap='kbc', clim=(1, np.nan),  #logz=True, 
    height=600, width=1000, xaxis=None, yaxis=None
)
points = df.hvplot.points(
    x='easting', y='northing', c='random',
    hover_cols=['name'], cmap=mag_cmap).opts(bgcolor='black') # .opts is described in the next notebook

pop_and_points = (rasterized_pop * points).relabel(title)
pop_and_points

:DynamicMap   []
   :Overlay
      .Image.I     :Image   [longitude,latitude]   (random)
      .Coastline.I :Feature   [Longitude,Latitude]
      .Points.I    :Points   [easting,northing]   (random,name)